In [1]:
import tensorflow as tf

import sys

In [2]:
from tensorflow.keras.applications import EfficientNetB4
from tensorflow.keras.layers.experimental import preprocessing
from tensorflow.keras.models import Sequential
from tensorflow.keras import layers
import tensorflow_datasets as tfds

import matplotlib.pyplot as plt
import numpy as np
import tensorflow as tf
from tensorflow import keras
from PIL import Image as Img

# For Grad-CAM
import xgradcam
from xgradcam import get_img_array
from xgradcam import make_gradcam_heatmap
from xgradcam import save_and_display_gradcam

from pathlib import Path
import os
import glob
import matplotlib.cm as cm 
from numpy import save
from numpy import load
from skimage.transform import resize
from tensorflow.keras.models import load_model
from tensorflow.keras.applications.resnet import preprocess_input as resnet_preprocessing
from tensorflow.keras.applications.inception_resnet_v2 import preprocess_input as inceptionresnet_preprocessing
from tensorflow.keras.applications.efficientnet import preprocess_input as efficientnet_preprocessing
from tensorflow.keras.applications.inception_v3 import preprocess_input as inception_preprocessing
from tensorflow.keras.applications.mobilenet import preprocess_input as mobilenet_preprocessing
from tensorflow.keras.applications.mobilenet_v2 import preprocess_input as mobilenetv2_preprocessing
from tensorflow.keras.applications.nasnet import preprocess_input as nasnet_preprocessing
from tensorflow.keras.applications.resnet_v2 import preprocess_input as resnetv2_preprocessing
from tensorflow.keras.applications.vgg16 import preprocess_input as vgg_preprocessing
from tensorflow.keras.applications.xception import preprocess_input as xception_preprocessing
from tensorflow.keras.preprocessing.image import ImageDataGenerator, DirectoryIterator

In [29]:
def save_and_display_gradcam(img, heatmap, cam_path='', alpha=0.4):
    # Load the original image
#     img = img_array[0]
    # Rescale heatmap to a range 0-255    
    heatmap = np.uint8(255 * heatmap)
    # Resize heatmap to save 
    heatmap_resized = resize(heatmap, (300, 400))

    # Use jet colormap to colorize heatmap
    jet = cm.get_cmap("jet")

    # Use RGB values of the colormap
    jet_colors = jet(np.arange(256))[:, :3]
    jet_heatmap = jet_colors[heatmap]

    # Create an image with RGB colorized heatmap
    jet_heatmap = keras.preprocessing.image.array_to_img(jet_heatmap)
    jet_heatmap = jet_heatmap.resize((img.size[0], img.size[1]))
    jet_heatmap = keras.preprocessing.image.img_to_array(jet_heatmap)

    # Superimpose the heatmap on original image
    superimposed_img = jet_heatmap * alpha + img
    superimposed_img = keras.preprocessing.image.array_to_img(superimposed_img)

    return superimposed_img, heatmap_resized

In [30]:
root_path = "/home/ubuntu/hot-store/final"
model_names = [
    "efficientnet", 
    "inception", 
    "inceptionresnet", 
    "mobilenetv1", 
    "mobilenetv2",
    "nasnetmobile",
    "resnet",
    "resnetv2",
    'vgg',
    "xception"
]
model_dirs = [Path(root_path) / model_name for model_name in model_names]
results_paths = [f"{model_dir}/visualisation/gradcam/" for model_dir in model_dirs]

model_infos = [
    {
        'model_name': 'resnet',
        'model_dir': f'{root_path}/resnet',
        'results_path': f"{root_path}/resnet/visualisation/gradcam/",
        'last_conv_layer_name': 'conv5_block3_out',
        'target_size': (400, 300),
        'preprocessing_function': resnet_preprocessing,    
    },
    {
        'model_name': 'efficientnet',
        'model_dir': f'{root_path}/efficientnet',
        'results_path': f"{root_path}/efficientnet/visualisation/gradcam/",
        'last_conv_layer_name': 'top_conv',
        'target_size': (400, 300),
        'preprocessing_function': efficientnet_preprocessing,    
    },
    {
        'model_name': 'inceptionresnet',
        'model_dir': f'{root_path}/inceptionresnet',
        'results_path': f"{root_path}/inceptionresnet/visualisation/gradcam/",
        'last_conv_layer_name': 'conv_7b',
        'target_size': (400, 300),
        'preprocessing_function': inceptionresnet_preprocessing,    
    },
    {
        'model_name': 'inception',
        'model_dir': f'{root_path}/inception',
        'results_path': f"{root_path}/inception/visualisation/gradcam/",
        'last_conv_layer_name': 'mixed10',
        'target_size': (400, 300),
        'preprocessing_function': inception_preprocessing,    
    },
    {
        'model_name': 'mobilenetv1',
        'model_dir': f'{root_path}/mobilenetv1',
        'results_path': f"{root_path}/mobilenetv1/visualisation/gradcam/",
        'last_conv_layer_name': 'conv_pw_13_relu',
        'target_size': (400, 300),
        'preprocessing_function': mobilenet_preprocessing,    
    },
    {
        'model_name': 'mobilenetv2',
        'model_dir': f'{root_path}/mobilenetv2',
        'results_path': f"{root_path}/mobilenetv2/visualisation/gradcam/",
        'last_conv_layer_name': 'out_relu',
        'target_size': (400, 300),
        'preprocessing_function': mobilenetv2_preprocessing,    
    },
    {
        'model_name': 'nasnetmobile',
        'model_dir': f'{root_path}/nasnetmobile',
        'results_path': f"{root_path}/nasnetmobile/visualisation/gradcam/",
        'last_conv_layer_name': 'activation_484',
        'target_size': (224, 224),
        'preprocessing_function': nasnet_preprocessing,    
    },
    {
        'model_name': 'resnetv2',
        'model_dir': f'{root_path}/resnetv2',
        'results_path': f"{root_path}/resnetv2/visualisation/gradcam/",
        'last_conv_layer_name': 'post_relu',
        'target_size': (400, 300),
        'preprocessing_function': resnetv2_preprocessing,    
    },
    {
        'model_name': 'vgg',
        'model_dir': f'{root_path}/vgg',
        'results_path': f"{root_path}/vgg/visualisation/gradcam/",
        'last_conv_layer_name': 'block5_conv3',
        'target_size': (400, 300),
        'preprocessing_function': vgg_preprocessing,    
    },
    {
        'model_name': 'xception',
        'model_dir': f'{root_path}/xception',
        'results_path': f"{root_path}/xception/visualisation/gradcam/",
        'last_conv_layer_name': 'block14_sepconv2_act',
        'target_size': (400, 300),
        'preprocessing_function': xception_preprocessing,    
    },
]

for model_info in model_infos:
    model_weights = glob.glob(f"{model_info['model_dir']}/*_finetuned.h5")
    
    for model_path in model_weights:
        model_name = Path(model_path).stem
        model_results_path = os.path.join(model_info['results_path'], model_name) 
        # create dir for each model
        if not os.path.exists(model_results_path):
            os.makedirs(model_results_path)

        model = load_model(Path(model_path))
        if model_name.startswith('vgg'):
            model.layers[-1].activation = None
        
        data_generator = ImageDataGenerator(
            fill_mode='nearest',
            preprocessing_function=model_info['preprocessing_function']
        )
        data_iterator = data_generator.flow_from_directory(
            '/home/ubuntu/hot-store/dermx_finetuning/split1/test', 
            batch_size=1, 
            target_size=model_info['target_size'],
            class_mode='categorical',
            follow_links=True,
            interpolation='bilinear',
            shuffle=False,
        )
        class_indices = data_iterator.class_indices

        for (img_array, label), img_path in zip(data_iterator, data_iterator.filepaths):
            img_name = Path(img_path).stem
            preds = model.predict(img_array)
            for category in class_indices:
                print(model_name, img_name, category)
                img = Img.open(img_path)
                heatmap = make_gradcam_heatmap(img_array, model, model_info['last_conv_layer_name'], class_indices[category])
                imposed, heat_map_resized = save_and_display_gradcam(img, heatmap)
                # save files
                save(model_results_path + '/' + img_name + '_' +  category + '.npy', heat_map_resized)
                imposed.save(model_results_path + '/' + img_name + '_' +  category + '.png')


Found 262 images belonging to 6 classes.
resnet50_r20_s0.5_z0.5_b[0.5, 1.5]_lr0.0001_lconv5_block3_out_0_finetuned 032462HB Acne
resnet50_r20_s0.5_z0.5_b[0.5, 1.5]_lr0.0001_lconv5_block3_out_0_finetuned 032462HB Actinic keratosis
resnet50_r20_s0.5_z0.5_b[0.5, 1.5]_lr0.0001_lconv5_block3_out_0_finetuned 032462HB Psoriasis
resnet50_r20_s0.5_z0.5_b[0.5, 1.5]_lr0.0001_lconv5_block3_out_0_finetuned 032462HB Seborrheic dermatitis
resnet50_r20_s0.5_z0.5_b[0.5, 1.5]_lr0.0001_lconv5_block3_out_0_finetuned 032462HB Viral warts
resnet50_r20_s0.5_z0.5_b[0.5, 1.5]_lr0.0001_lconv5_block3_out_0_finetuned 032462HB Vitiligo
resnet50_r20_s0.5_z0.5_b[0.5, 1.5]_lr0.0001_lconv5_block3_out_0_finetuned 032720HB Acne
resnet50_r20_s0.5_z0.5_b[0.5, 1.5]_lr0.0001_lconv5_block3_out_0_finetuned 032720HB Actinic keratosis
resnet50_r20_s0.5_z0.5_b[0.5, 1.5]_lr0.0001_lconv5_block3_out_0_finetuned 032720HB Psoriasis
resnet50_r20_s0.5_z0.5_b[0.5, 1.5]_lr0.0001_lconv5_block3_out_0_finetuned 032720HB Seborrheic dermatiti

resnet50_r20_s0.5_z0.5_b[0.5, 1.5]_lr0.0001_lconv5_block3_out_0_finetuned 034686HB Acne
resnet50_r20_s0.5_z0.5_b[0.5, 1.5]_lr0.0001_lconv5_block3_out_0_finetuned 034686HB Actinic keratosis
resnet50_r20_s0.5_z0.5_b[0.5, 1.5]_lr0.0001_lconv5_block3_out_0_finetuned 034686HB Psoriasis
resnet50_r20_s0.5_z0.5_b[0.5, 1.5]_lr0.0001_lconv5_block3_out_0_finetuned 034686HB Seborrheic dermatitis
resnet50_r20_s0.5_z0.5_b[0.5, 1.5]_lr0.0001_lconv5_block3_out_0_finetuned 034686HB Viral warts
resnet50_r20_s0.5_z0.5_b[0.5, 1.5]_lr0.0001_lconv5_block3_out_0_finetuned 034686HB Vitiligo
resnet50_r20_s0.5_z0.5_b[0.5, 1.5]_lr0.0001_lconv5_block3_out_0_finetuned 034695HB Acne
resnet50_r20_s0.5_z0.5_b[0.5, 1.5]_lr0.0001_lconv5_block3_out_0_finetuned 034695HB Actinic keratosis
resnet50_r20_s0.5_z0.5_b[0.5, 1.5]_lr0.0001_lconv5_block3_out_0_finetuned 034695HB Psoriasis
resnet50_r20_s0.5_z0.5_b[0.5, 1.5]_lr0.0001_lconv5_block3_out_0_finetuned 034695HB Seborrheic dermatitis
resnet50_r20_s0.5_z0.5_b[0.5, 1.5]_lr0.

resnet50_r20_s0.5_z0.5_b[0.5, 1.5]_lr0.0001_lconv5_block3_out_0_finetuned 2652--WatermarkedWyJXYXRlcm1hcmtlZCJd Seborrheic dermatitis
resnet50_r20_s0.5_z0.5_b[0.5, 1.5]_lr0.0001_lconv5_block3_out_0_finetuned 2652--WatermarkedWyJXYXRlcm1hcmtlZCJd Viral warts
resnet50_r20_s0.5_z0.5_b[0.5, 1.5]_lr0.0001_lconv5_block3_out_0_finetuned 2652--WatermarkedWyJXYXRlcm1hcmtlZCJd Vitiligo
resnet50_r20_s0.5_z0.5_b[0.5, 1.5]_lr0.0001_lconv5_block3_out_0_finetuned a-fulm2--WatermarkedWyJXYXRlcm1hcmtlZCJd Acne
resnet50_r20_s0.5_z0.5_b[0.5, 1.5]_lr0.0001_lconv5_block3_out_0_finetuned a-fulm2--WatermarkedWyJXYXRlcm1hcmtlZCJd Actinic keratosis
resnet50_r20_s0.5_z0.5_b[0.5, 1.5]_lr0.0001_lconv5_block3_out_0_finetuned a-fulm2--WatermarkedWyJXYXRlcm1hcmtlZCJd Psoriasis
resnet50_r20_s0.5_z0.5_b[0.5, 1.5]_lr0.0001_lconv5_block3_out_0_finetuned a-fulm2--WatermarkedWyJXYXRlcm1hcmtlZCJd Seborrheic dermatitis
resnet50_r20_s0.5_z0.5_b[0.5, 1.5]_lr0.0001_lconv5_block3_out_0_finetuned a-fulm2--WatermarkedWyJXYXRlcm1h

resnet50_r20_s0.5_z0.5_b[0.5, 1.5]_lr0.0001_lconv5_block3_out_0_finetuned acne-face-2-31--WatermarkedWyJXYXRlcm1hcmtlZCJd Vitiligo
resnet50_r20_s0.5_z0.5_b[0.5, 1.5]_lr0.0001_lconv5_block3_out_0_finetuned acne-face-2-6--WatermarkedWyJXYXRlcm1hcmtlZCJd Acne
resnet50_r20_s0.5_z0.5_b[0.5, 1.5]_lr0.0001_lconv5_block3_out_0_finetuned acne-face-2-6--WatermarkedWyJXYXRlcm1hcmtlZCJd Actinic keratosis
resnet50_r20_s0.5_z0.5_b[0.5, 1.5]_lr0.0001_lconv5_block3_out_0_finetuned acne-face-2-6--WatermarkedWyJXYXRlcm1hcmtlZCJd Psoriasis
resnet50_r20_s0.5_z0.5_b[0.5, 1.5]_lr0.0001_lconv5_block3_out_0_finetuned acne-face-2-6--WatermarkedWyJXYXRlcm1hcmtlZCJd Seborrheic dermatitis
resnet50_r20_s0.5_z0.5_b[0.5, 1.5]_lr0.0001_lconv5_block3_out_0_finetuned acne-face-2-6--WatermarkedWyJXYXRlcm1hcmtlZCJd Viral warts
resnet50_r20_s0.5_z0.5_b[0.5, 1.5]_lr0.0001_lconv5_block3_out_0_finetuned acne-face-2-6--WatermarkedWyJXYXRlcm1hcmtlZCJd Vitiligo
resnet50_r20_s0.5_z0.5_b[0.5, 1.5]_lr0.0001_lconv5_block3_out_0_fin

resnet50_r20_s0.5_z0.5_b[0.5, 1.5]_lr0.0001_lconv5_block3_out_0_finetuned acne-face-65--WatermarkedWyJXYXRlcm1hcmtlZCJd Actinic keratosis
resnet50_r20_s0.5_z0.5_b[0.5, 1.5]_lr0.0001_lconv5_block3_out_0_finetuned acne-face-65--WatermarkedWyJXYXRlcm1hcmtlZCJd Psoriasis
resnet50_r20_s0.5_z0.5_b[0.5, 1.5]_lr0.0001_lconv5_block3_out_0_finetuned acne-face-65--WatermarkedWyJXYXRlcm1hcmtlZCJd Seborrheic dermatitis
resnet50_r20_s0.5_z0.5_b[0.5, 1.5]_lr0.0001_lconv5_block3_out_0_finetuned acne-face-65--WatermarkedWyJXYXRlcm1hcmtlZCJd Viral warts
resnet50_r20_s0.5_z0.5_b[0.5, 1.5]_lr0.0001_lconv5_block3_out_0_finetuned acne-face-65--WatermarkedWyJXYXRlcm1hcmtlZCJd Vitiligo
resnet50_r20_s0.5_z0.5_b[0.5, 1.5]_lr0.0001_lconv5_block3_out_0_finetuned acne-face-66--WatermarkedWyJXYXRlcm1hcmtlZCJd Acne
resnet50_r20_s0.5_z0.5_b[0.5, 1.5]_lr0.0001_lconv5_block3_out_0_finetuned acne-face-66--WatermarkedWyJXYXRlcm1hcmtlZCJd Actinic keratosis
resnet50_r20_s0.5_z0.5_b[0.5, 1.5]_lr0.0001_lconv5_block3_out_0_fi

...

xception_r10_s0.25_z0.5_b[0.5, 1.5]_lr0.001_lblock14_sepconv2_act_2_finetuned acne-face-3-12--WatermarkedWyJXYXRlcm1hcmtlZCJd Viral warts
xception_r10_s0.25_z0.5_b[0.5, 1.5]_lr0.001_lblock14_sepconv2_act_2_finetuned acne-face-3-12--WatermarkedWyJXYXRlcm1hcmtlZCJd Vitiligo
xception_r10_s0.25_z0.5_b[0.5, 1.5]_lr0.001_lblock14_sepconv2_act_2_finetuned acne-face-3-13--WatermarkedWyJXYXRlcm1hcmtlZCJd Acne
xception_r10_s0.25_z0.5_b[0.5, 1.5]_lr0.001_lblock14_sepconv2_act_2_finetuned acne-face-3-13--WatermarkedWyJXYXRlcm1hcmtlZCJd Actinic keratosis
xception_r10_s0.25_z0.5_b[0.5, 1.5]_lr0.001_lblock14_sepconv2_act_2_finetuned acne-face-3-13--WatermarkedWyJXYXRlcm1hcmtlZCJd Psoriasis
xception_r10_s0.25_z0.5_b[0.5, 1.5]_lr0.001_lblock14_sepconv2_act_2_finetuned acne-face-3-13--WatermarkedWyJXYXRlcm1hcmtlZCJd Seborrheic dermatitis
xception_r10_s0.25_z0.5_b[0.5, 1.5]_lr0.001_lblock14_sepconv2_act_2_finetuned acne-face-3-13--WatermarkedWyJXYXRlcm1hcmtlZCJd Viral warts
xception_r10_s0.25_z0.5_b[0.5,

xception_r10_s0.25_z0.5_b[0.5, 1.5]_lr0.001_lblock14_sepconv2_act_2_finetuned acne-face-66--WatermarkedWyJXYXRlcm1hcmtlZCJd Viral warts
xception_r10_s0.25_z0.5_b[0.5, 1.5]_lr0.001_lblock14_sepconv2_act_2_finetuned acne-face-66--WatermarkedWyJXYXRlcm1hcmtlZCJd Vitiligo
xception_r10_s0.25_z0.5_b[0.5, 1.5]_lr0.001_lblock14_sepconv2_act_2_finetuned acne-face-75--WatermarkedWyJXYXRlcm1hcmtlZCJd Acne
xception_r10_s0.25_z0.5_b[0.5, 1.5]_lr0.001_lblock14_sepconv2_act_2_finetuned acne-face-75--WatermarkedWyJXYXRlcm1hcmtlZCJd Actinic keratosis
xception_r10_s0.25_z0.5_b[0.5, 1.5]_lr0.001_lblock14_sepconv2_act_2_finetuned acne-face-75--WatermarkedWyJXYXRlcm1hcmtlZCJd Psoriasis
xception_r10_s0.25_z0.5_b[0.5, 1.5]_lr0.001_lblock14_sepconv2_act_2_finetuned acne-face-75--WatermarkedWyJXYXRlcm1hcmtlZCJd Seborrheic dermatitis
xception_r10_s0.25_z0.5_b[0.5, 1.5]_lr0.001_lblock14_sepconv2_act_2_finetuned acne-face-75--WatermarkedWyJXYXRlcm1hcmtlZCJd Viral warts
xception_r10_s0.25_z0.5_b[0.5, 1.5]_lr0.001_

xception_r10_s0.25_z0.5_b[0.5, 1.5]_lr0.001_lblock14_sepconv2_act_2_finetuned 016641HB Psoriasis
xception_r10_s0.25_z0.5_b[0.5, 1.5]_lr0.001_lblock14_sepconv2_act_2_finetuned 016641HB Seborrheic dermatitis
xception_r10_s0.25_z0.5_b[0.5, 1.5]_lr0.001_lblock14_sepconv2_act_2_finetuned 016641HB Viral warts
xception_r10_s0.25_z0.5_b[0.5, 1.5]_lr0.001_lblock14_sepconv2_act_2_finetuned 016641HB Vitiligo
xception_r10_s0.25_z0.5_b[0.5, 1.5]_lr0.001_lblock14_sepconv2_act_2_finetuned 016680HB Acne
xception_r10_s0.25_z0.5_b[0.5, 1.5]_lr0.001_lblock14_sepconv2_act_2_finetuned 016680HB Actinic keratosis
xception_r10_s0.25_z0.5_b[0.5, 1.5]_lr0.001_lblock14_sepconv2_act_2_finetuned 016680HB Psoriasis
xception_r10_s0.25_z0.5_b[0.5, 1.5]_lr0.001_lblock14_sepconv2_act_2_finetuned 016680HB Seborrheic dermatitis
xception_r10_s0.25_z0.5_b[0.5, 1.5]_lr0.001_lblock14_sepconv2_act_2_finetuned 016680HB Viral warts
xception_r10_s0.25_z0.5_b[0.5, 1.5]_lr0.001_lblock14_sepconv2_act_2_finetuned 016680HB Vitiligo
x

xception_r10_s0.25_z0.5_b[0.5, 1.5]_lr0.001_lblock14_sepconv2_act_2_finetuned 249--WatermarkedWyJXYXRlcm1hcmtlZCJd Viral warts
xception_r10_s0.25_z0.5_b[0.5, 1.5]_lr0.001_lblock14_sepconv2_act_2_finetuned 249--WatermarkedWyJXYXRlcm1hcmtlZCJd Vitiligo
xception_r10_s0.25_z0.5_b[0.5, 1.5]_lr0.001_lblock14_sepconv2_act_2_finetuned 269--WatermarkedWyJXYXRlcm1hcmtlZCJd Acne
xception_r10_s0.25_z0.5_b[0.5, 1.5]_lr0.001_lblock14_sepconv2_act_2_finetuned 269--WatermarkedWyJXYXRlcm1hcmtlZCJd Actinic keratosis
xception_r10_s0.25_z0.5_b[0.5, 1.5]_lr0.001_lblock14_sepconv2_act_2_finetuned 269--WatermarkedWyJXYXRlcm1hcmtlZCJd Psoriasis
xception_r10_s0.25_z0.5_b[0.5, 1.5]_lr0.001_lblock14_sepconv2_act_2_finetuned 269--WatermarkedWyJXYXRlcm1hcmtlZCJd Seborrheic dermatitis
xception_r10_s0.25_z0.5_b[0.5, 1.5]_lr0.001_lblock14_sepconv2_act_2_finetuned 269--WatermarkedWyJXYXRlcm1hcmtlZCJd Viral warts


IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)

